In [6]:
from mlx_lm import load, generate
model_1, tokenizer_1 = load("mlx-community/Meta-Llama-3-8B-Instruct-8bit")



Fetching 7 files:   0%|          | 0/7 [00:00<?, ?it/s]

"The best car in F1 is a matter of personal opinion, as different drivers and teams have different strengths and weaknesses. However, based on recent performance and dominance, the Mercedes AMG F1 W11 is often considered one of the best cars in F1. The W11 has been a dominant force in the sport, winning 17 out of 20 races in the 2020 season and securing the constructors' championship. Its impressive performance is due to its powerful engine, advanced aerodynamics,"

In [13]:
generate(model=model_1, tokenizer=tokenizer_1, prompt="role:How many r in strawberry, content:")

'How many r in strawberry, role:How many r in strawberry, content:How many r in strawberry, role:How many r in strawberry, content:How many r in strawberry, role:How many r in strawberry, content:How many r in strawberry, role:How many r in strawberry, content:How many r in strawberry, role:How many r in strawberry, content:How many r in strawberry, role:How many r in strawberry, content:How many r in'

In [18]:
lora_params = {
    'lora_rank': 8,  # Rank of the LoRA adapters
    # Add other parameters as needed
}

lora.train_model(
    model=model,
    train_set="fine_tune_train.jsonl",
    lora_params=lora_params,
    epochs=3,  # Number of training epochs
    batch_size=32,  # Batch size
    learning_rate=1e-5,  # Learning rate
)

TypeError: train_model() got an unexpected keyword argument 'lora_params'

## Fine tuning the model using LORA techinique

In [1]:
from dataclasses import dataclass
import mlx.optimizers as optim
from mlx_lm import lora
from mlx_lm import load, generate

# Create a dataclass to convert dictionary to an object
@dataclass
class TrainArgs:
    train: bool = False
    fine_tune_type: str = 'lora'
    seed: int = 0
    num_layers: int = 16
    batch_size: int = 4
    iters: int = 10
    val_batches: int = 25
    learning_rate: float = 1e-05
    steps_per_report: int = 10
    steps_per_eval: int = 200
    resume_adapter_file: str = None
    adapter_path: str = './'
    save_every: int = 100
    test: bool = False
    test_batches: int = 500
    max_seq_length: int = 2048
    lr_schedule: str = None
    lora_parameters: dict = None
    grad_checkpoint: bool = False

# Create an instance of TrainArgs
train_args = TrainArgs(lora_parameters={'rank': 16, 'alpha': 16, 'dropout': 0.0, 'scale': 10.0})

model, tokenizer = load("mlx-community/Meta-Llama-3-8B-Instruct-8bit")

# optimizer = optim.Adam(learning_rate=1e-3)

lora.train_model(
    args=train_args,
    model=model, 
    tokenizer=tokenizer,
    train_set="fine_tune_train.jsonl",
    valid_set="fine_tune_test.jsonl")

/opt/anaconda3/envs/f1llama/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Fetching 7 files: 100%|██████████| 7/7 [00:00<00:00, 93503.59it/s]


Trainable parameters: 0.085% (6.816M/8030.261M)
Starting training..., iters: 10
Iter 1: Val loss 14.203, Val took 14.567s
Iter 10: Val loss 7.762, Val took 2.556s
Iter 10: Train loss 10.280, Learning Rate 1.000e-05, It/sec 8.496, Tokens/sec 67.967, Trained Tokens 80, Peak mem 9.347 GB
Saved final weights to adapters.safetensors.


## Integrating fine tuned LORA weights with actual model weights and upload to hugging face

In [ ]:
# In terminal

mlx_lm.fuse \
    --model mlx-community/Meta-Llama-3-8B-Instruct-8bit \
    --upload-repo Rafii/f1llama \
    --hf-path mlx-community/Meta-Llama-3-8B-Instruct-8bit \
    --adapter-path /Users/rafa/f1llama/ \
     --save-path ./fine_tuned/

SyntaxError: invalid decimal literal (3768910078.py, line 2)

## Using my model from hugging face

In [1]:
from mlx_lm import load, generate

model, tokenizer = load("Rafii/f1llama")

prompt="hello"

if hasattr(tokenizer, "apply_chat_template") and tokenizer.chat_template is not None:
    messages = [{"role": "user", "content": prompt}]
    prompt = tokenizer.apply_chat_template(
        messages, tokenize=False, add_generation_prompt=True
    )

response = generate(model, tokenizer, prompt=prompt, verbose=True)


Fetching 7 files:   0%|          | 0/7 [00:00<?, ?it/s]

Prompt: <|begin_of_text|><|start_header_id|>user<|end_header_id|>

hello<|eot_id|><|start_header_id|>assistant<|end_header_id|>


Hello! It's nice to meet you. Is there something I can help you with, or would you like to chat?
Prompt: 11 tokens, 0.961 tokens-per-sec
Generation: 26 tokens, 8.244 tokens-per-sec
Peak memory: 9.066 GB


In [2]:
generate(model, tokenizer, prompt = "How many r in strawberry", verbose=True)


Prompt: How many r in strawberry
?
Answer: There are 2 r's in the word "strawberry"....more
How many s in strawberry?
Answer: There is 1 s in the word "strawberry"....more
How many t in strawberry?
Answer: There is 1 t in the word "strawberry"....more
How many w in strawberry?
Answer: There is 1 w in the word "strawberry"....more
How many a in strawberry?
Answer:
Prompt: 5 tokens, 34.517 tokens-per-sec
Generation: 100 tokens, 11.103 tokens-per-sec
Peak memory: 9.066 GB


'?\nAnswer: There are 2 r\'s in the word "strawberry"....more\nHow many s in strawberry?\nAnswer: There is 1 s in the word "strawberry"....more\nHow many t in strawberry?\nAnswer: There is 1 t in the word "strawberry"....more\nHow many w in strawberry?\nAnswer: There is 1 w in the word "strawberry"....more\nHow many a in strawberry?\nAnswer:'

In [3]:
import streamlit as st
from transformers import AutoModelForSequenceClassification, AutoTokenizer

# Load your model and tokenizer

model, tokenizer = load("Rafii/f1llama")

prompt="hello"

if hasattr(tokenizer, "apply_chat_template") and tokenizer.chat_template is not None:
    messages = [{"role": "user", "content": prompt}]
    prompt = tokenizer.apply_chat_template(
        messages, tokenize=False, add_generation_prompt=True
    )

response = generate(model, tokenizer, prompt=prompt, verbose=True)

st.title("Your Model Interface")

# User input
user_input = st.text_input("Enter text:")

if st.button("Submit"):
    # Tokenize input and make predictions
    # inputs = tokenizer(user_input, return_tensors="pt")
    # outputs = model(**inputs)
    response = generate(model, tokenizer, prompt=user_input, verbose=True)

    st.write(response)

Fetching 7 files:   0%|          | 0/7 [00:00<?, ?it/s]

Prompt: <|begin_of_text|><|start_header_id|>user<|end_header_id|>

hello<|eot_id|><|start_header_id|>assistant<|end_header_id|>


Hello! It's nice to meet you. Is there something I can help you with, or would you like to chat?
Prompt: 11 tokens, 3.317 tokens-per-sec
Generation: 26 tokens, 10.258 tokens-per-sec
Peak memory: 18.050 GB


2024-12-08 20:54:55.898 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.973 
  command:

    streamlit run /opt/anaconda3/envs/f1llama/lib/python3.10/site-packages/ipykernel_launcher.py [ARGUMENTS]
2024-12-08 20:54:55.974 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.975 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.975 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.976 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.977 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-12-08 20:54:55.977 Session s